### import modules

In [1]:
import pandas as pd
import numpy as np
from numpy import dot
from numpy.linalg import norm
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle

### dealing with data

In [39]:
path = 'BlackFriday.csv'
data = pd.read_csv(path)
data = data.drop(['Gender', 'Age', 'Occupation', 'City_Category',
                  'Stay_In_Current_City_Years', 'Marital_Status',
                  'Product_Category_1', 'Product_Category_2',
                  'Product_Category_3', 'Purchase'], axis=1)

data2 = data.groupby(['User_ID']).count()
df = pd.DataFrame({'User_ID':data2['Product_ID'].index, 'countProduct':data2['Product_ID'].values})
data = data.join(df.set_index('User_ID'), on='User_ID').sort_values(['User_ID'])

# drop data whose countProduct is less than 300
data = data[data.countProduct >= 300]
data = data.reset_index(drop = True)

# data about users (312 users)
users = pd.DataFrame(data.User_ID.unique())
users.columns = ['User_ID']
users_length = len(users)

# data about products
products = pd.DataFrame(data.Product_ID.unique())
products.columns = ['Product_ID']
products_length = len(products)

data['purchased'] = 1

df_matrix = pd.pivot_table(data, values='purchased', index='User_ID', columns='Product_ID', fill_value=0)

# df has user and countProduct whose countProduct >= 300
user_cnt_info = pd.DataFrame({'User_ID':data['User_ID'], 'countProduct':data['countProduct']})
user_cnt_info = user_cnt_info.groupby(['User_ID', 'countProduct']).count().reset_index()

### split the data and store

In [ ]:
'''train, val, test data 를 만드는 cell => 초기에만 실행할 것'''

test = pd.DataFrame()
val = pd.DataFrame()
train = pd.DataFrame()

i = 0
j = 0

while i < len(data):
    cnt = data.loc[i].countProduct
    tmp = data[i: i+cnt]
    tmp = shuffle(tmp).reset_index()
    test = test.append(tmp[0:10])
    val = val.append(tmp[10:20])
    train = train.append(tmp[20:])
    j = j + 1
    i = i + cnt
    
train.to_csv("train_data.csv", mode='w')
val.to_csv("val_data.csv", mode='w')
test.to_csv("test_data.csv", mode='w')

In [64]:
'''저장되어 있는 train, val, test data 를 사용하는 경우 실행.'''

train = pd.read_csv('train_data.csv')
val = pd.read_csv('val_data.csv')
test = pd.read_csv('test_data.csv')

train = train.drop(['Unnamed: 0', 'index'], axis=1)
val = val.drop(['Unnamed: 0', 'index'], axis=1)
test =test.drop(['Unnamed: 0', 'index'], axis=1)

In [158]:
train_matrix = pd.pivot_table(train, values='purchased', index='User_ID', columns='Product_ID', fill_value=0)

train_products = pd.DataFrame(train.Product_ID.unique())
train_products.columns = ['Product_ID']
train_products_length = len(train_products)

val_matrix = pd.pivot_table(val, values='purchased', index='User_ID', columns='Product_ID', fill_value=0)

val_products = pd.DataFrame(val.Product_ID.unique())
val_products.columns = ['Product_ID']
val_products = val_products.sort_values('Product_ID')
val_products_length = len(val_products)

val_user_info = pd.DataFrame(val.User_ID.unique())
val_user_info.columns = ['User_ID']
val_users_length = len(val_user_info)

### defining cosine similarity module

In [229]:
def cos_sim(A, B):
    if(norm(A)==0 or norm(B)==0):
        return 0
    else:
        return dot(A, B)/(norm(A)*norm(B))    

### user based CF

#### user - user 사이의 유사도를 계산함.

In [ ]:
'''user_user matrix 를 만드는 cell => 초기에만 실행할 것'''
#user 사이의 유사도를 계산함.
user_user_matrix = np.zeros(shape=(users_length,users_length))

i = 0
j = 0
for user1 in users['User_ID']:
    user_1 = np.array(train_matrix.loc[user1])
    j = 0
    for user2 in users['User_ID']:
        user_2 = np.array(train_matrix.loc[user2])
        user_user_matrix[i][j] = cos_sim(user_1, user_2)
        j = j+1
    i = i+1
    
np.savetxt('user_user_matrix.csv', user_user_matrix, delimiter=',')

In [21]:
'''저장한 user_user matrix를 이용하는 경우 실행함.'''
user_user_matrix = pd.read_csv('user_user_matrix.csv', header = None)

In [253]:
user_user_matrix.describe()

0           1           2           3           4           5    \
count  312.000000  312.000000  312.000000  312.000000  312.000000  312.000000   
mean     0.242877    0.222935    0.220627    0.213614    0.213681    0.236882   
std      0.059481    0.054777    0.058278    0.061369    0.057937    0.053603   
min      0.088991    0.125844    0.083959    0.072775    0.097439    0.111906   
25%      0.214899    0.196530    0.194169    0.185287    0.188138    0.214224   
50%      0.243309    0.220826    0.219788    0.214015    0.211697    0.236056   
75%      0.270836    0.242606    0.244294    0.238391    0.236562    0.255225   
max      1.000000    1.000000    1.000000    1.000000    1.000000    1.000000   

              6           7           8           9       ...             302  \
count  312.000000  312.000000  312.000000  312.000000     ...      312.000000   
mean     0.166566    0.224203    0.238222    0.222579     ...        0.268221   
std      0.063260    0.054565    0.059990    0.058826     ...        0.056260   
min      0.064847    0.126576    0.098041    0.072942     ...        0.103102   
25%      0.135364    0.199422    0.208905    0.197063     ...        0.241843   
50%      0.163021    0.224248    0.240938    0.217236     ...        0.264620   
75%      0.191840    0.245590    0.265239    0.248056     ...        0.290764   
max      1.000000    1.000000    1.000000    1.000000     ...        1.000000   

              303         304         305         306         307         308  \
count  312.000000  312.000000  312.000000  312.000000  312.000000  312.000000   
mean     0.194097    0.231013    0.205481    0.180260    0.246505    0.216667   
std      0.055223    0.054030    0.058368    0.058040    0.060089    0.056808   
min      0.088291    0.087887    0.054354    0.075857    0.089603    0.118913   
25%      0.171114    0.206106    0.181502    0.155551    0.216800    0.190057   
50%      0.192780    0.229900    0.204677    0.178914    0.246273    0.217652   
75%      0.209289    0.249275    0.226769    0.200257    0.269501    0.238211   
max      1.000000    1.000000    1.000000    1.000000    1.000000    1.000000   

              309         310         311  
count  312.000000  312.000000  312.000000  
mean     0.223584    0.222106    0.207580  
std      0.056586    0.056563    0.053698  
min      0.077267    0.106662    0.116916  
25%      0.196680    0.195244    0.184093  
50%      0.225656    0.222008    0.202969  
75%      0.248802    0.243202    0.226811  
max      1.000000    1.000000    1.000000  

[8 rows x 312 columns]

#### 유사도가 높은 5명의 user 로 부터 추천 받아 recom_matrix 에 저장.
- cosine similarity > 0.3 이상 인 user 를 similar 하다고 할 것임.

In [254]:
'''recom_matrix 를 계산해야 하는 경우 실행함.'''
# recommendation matrix
recom_matrix = np.zeros(shape=(users_length,products_length))

i = 0
j = 0
cnt = 0
# user i와 j가 유사할 경우, i 에게 j가 산 물건을 추천한다. 

while(i<users_length):
    j = i+1
    cnt = 0
    while(j<users_length) :
        if(user_user_matrix.loc[i][j] > 0.3 and cnt < 5):
            cnt = cnt+1
            for k, product in enumerate(train_products['Product_ID']):
                # i 가 사지 않은 물건인데, j가 샀을 경우 i 에게 추천.
                if(train_matrix.loc[users.loc[i]][product].values==0 and 
                   train_matrix.loc[users.loc[j]][product].values==1):
                    print(i, k)
                    recom_matrix[i][k] = 1
                    print(recom_matrix[i][k])
        if (cnt == 5):
            break;
        j = j+1
    i = i+1

0 328
1.0
0 359
1.0
0 370
1.0
0 377
1.0
0 384
1.0
0 391
1.0
0 401
1.0
0 425
1.0
0 427
1.0
0 428
1.0
0 434
1.0
0 448
1.0
0 476
1.0
0 480
1.0
0 481
1.0
0 485
1.0
0 486
1.0
0 487
1.0
0 489
1.0
0 491
1.0
0 498
1.0
0 500
1.0
0 502
1.0
0 511
1.0
0 512
1.0
0 523
1.0
0 530
1.0
0 531
1.0
0 538
1.0
0 540
1.0
0 542
1.0
0 553
1.0
0 565
1.0
0 566
1.0
0 567
1.0
0 568
1.0
0 573
1.0
0 577
1.0
0 585
1.0
0 592
1.0
0 597
1.0
0 632
1.0
0 634
1.0
0 635
1.0
0 642
1.0
0 644
1.0
0 649
1.0
0 651
1.0
0 652
1.0
0 654
1.0
0 657
1.0
0 668
1.0
0 673
1.0
0 682
1.0
0 683
1.0
0 694
1.0
0 708
1.0
0 710
1.0
0 711
1.0
0 722
1.0
0 723
1.0
0 724
1.0
0 725
1.0
0 735
1.0
0 737
1.0
0 739
1.0
0 743
1.0
0 753
1.0
0 757
1.0
0 760
1.0
0 774
1.0
0 777
1.0
0 786
1.0
0 790
1.0
0 797
1.0
0 802
1.0
0 804
1.0
0 805
1.0
0 806
1.0
0 807
1.0
0 808
1.0
0 809
1.0
0 810
1.0
0 811
1.0
0 812
1.0
0 813
1.0
0 814
1.0
0 815
1.0
0 816
1.0
0 817
1.0
0 818
1.0
0 819
1.0
0 820
1.0
0 821
1.0
0 822
1.0
0 823
1.0
0 824
1.0
0 825
1.0
0 826
1.0
0 827
1.0


0 1796
1.0
0 1797
1.0
0 1798
1.0
0 1799
1.0
0 1800
1.0
0 1801
1.0
0 1802
1.0
0 1803
1.0
0 1804
1.0
0 1805
1.0
0 1806
1.0
0 1807
1.0
0 1808
1.0
0 1809
1.0
0 1810
1.0
0 1811
1.0
0 1812
1.0
0 1813
1.0
0 1814
1.0
0 1815
1.0
0 1816
1.0
0 1817
1.0
0 1818
1.0
0 1819
1.0
0 321
1.0
0 327
1.0
0 330
1.0
0 346
1.0
0 359
1.0
0 364
1.0
0 370
1.0
0 371
1.0
0 373
1.0
0 377
1.0
0 383
1.0
0 386
1.0
0 387
1.0
0 388
1.0
0 389
1.0
0 399
1.0
0 404
1.0
0 405
1.0
0 415
1.0
0 418
1.0
0 422
1.0
0 426
1.0
0 434
1.0
0 440
1.0
0 446
1.0
0 450
1.0
0 454
1.0
0 455
1.0
0 456
1.0
0 460
1.0
0 461
1.0
0 474
1.0
0 476
1.0
0 480
1.0
0 485
1.0
0 488
1.0
0 489
1.0
0 501
1.0
0 503
1.0
0 504
1.0
0 509
1.0
0 512
1.0
0 514
1.0
0 518
1.0
0 527
1.0
0 536
1.0
0 540
1.0
0 549
1.0
0 552
1.0
0 553
1.0
0 560
1.0
0 573
1.0
0 583
1.0
0 592
1.0
0 593
1.0
0 594
1.0
0 598
1.0
0 604
1.0
0 608
1.0
0 623
1.0
0 631
1.0
0 632
1.0
0 636
1.0
0 652
1.0
0 663
1.0
0 669
1.0
0 670
1.0
0 676
1.0
0 677
1.0
0 678
1.0
0 680
1.0
0 691
1.0
0 699
1.0
0 700


1 1246
1.0
1 1257
1.0
1 1265
1.0
1 1273
1.0
1 1275
1.0
1 1280
1.0
1 1284
1.0
1 1289
1.0
1 1290
1.0
1 1295
1.0
1 1296
1.0
1 1298
1.0
1 1302
1.0
1 1303
1.0
1 1313
1.0
1 1315
1.0
1 1318
1.0
1 1322
1.0
1 1326
1.0
1 1329
1.0
1 1332
1.0
1 1344
1.0
1 1346
1.0
1 1347
1.0
1 1352
1.0
1 1360
1.0
1 1365
1.0
1 1369
1.0
1 1371
1.0
1 1372
1.0
1 1376
1.0
1 1380
1.0
1 1382
1.0
1 1385
1.0
1 1392
1.0
1 1396
1.0
1 1400
1.0
1 1412
1.0
1 1418
1.0
1 1421
1.0
1 1429
1.0
1 1437
1.0
1 1443
1.0
1 1444
1.0
1 1445
1.0
1 1446
1.0
1 1448
1.0
1 1450
1.0
1 1452
1.0
1 1462
1.0
1 1464
1.0
1 1465
1.0
1 1469
1.0
1 1471
1.0
1 1476
1.0
1 1481
1.0
1 1483
1.0
1 1487
1.0
1 1492
1.0
1 1493
1.0
1 1498
1.0
1 1499
1.0
1 1502
1.0
1 1508
1.0
1 1509
1.0
1 1518
1.0
1 1523
1.0
1 1525
1.0
1 1526
1.0
1 1533
1.0
1 1534
1.0
1 1544
1.0
1 1550
1.0
1 1558
1.0
1 1559
1.0
1 1563
1.0
1 1572
1.0
1 1575
1.0
1 1576
1.0
1 1579
1.0
1 1580
1.0
1 1581
1.0
1 1583
1.0
1 1590
1.0
1 1591
1.0
1 1603
1.0
1 1608
1.0
1 1612
1.0
1 1622
1.0
1 1624
1.0
1 1629
1.0

2 2828
1.0
2 2841
1.0
2 2846
1.0
2 2863
1.0
2 2888
1.0
2 2903
1.0
2 2929
1.0
2 2985
1.0
2 2989
1.0
2 2995
1.0
2 3008
1.0
2 3013
1.0
2 3036
1.0
2 3040
1.0
2 3047
1.0
2 3081
1.0
2 3087
1.0
2 3092
1.0
2 3126
1.0
2 3150
1.0
2 3267
1.0
2 3294
1.0
2 3329
1.0
2 3335
1.0
2 3357
1.0
2 3375
1.0
2 3379
1.0
3 3
1.0
3 9
1.0
3 15
1.0
3 20
1.0
3 24
1.0
3 26
1.0
3 27
1.0
3 30
1.0
3 31
1.0
3 38
1.0
3 39
1.0
3 40
1.0
3 43
1.0
3 46
1.0
3 48
1.0
3 49
1.0
3 53
1.0
3 62
1.0
3 68
1.0
3 69
1.0
3 73
1.0
3 75
1.0
3 77
1.0
3 79
1.0
3 83
1.0
3 85
1.0
3 89
1.0
3 91
1.0
3 98
1.0
3 101
1.0
3 103
1.0
3 107
1.0
3 113
1.0
3 115
1.0
3 117
1.0
3 118
1.0
3 120
1.0
3 127
1.0
3 135
1.0
3 137
1.0
3 139
1.0
3 140
1.0
3 145
1.0
3 146
1.0
3 153
1.0
3 155
1.0
3 157
1.0
3 162
1.0
3 164
1.0
3 167
1.0
3 168
1.0
3 174
1.0
3 176
1.0
3 178
1.0
3 182
1.0
3 183
1.0
3 188
1.0
3 193
1.0
3 195
1.0
3 198
1.0
3 200
1.0
3 203
1.0
3 204
1.0
3 213
1.0
3 215
1.0
3 217
1.0
3 220
1.0
3 221
1.0
3 222
1.0
3 230
1.0
3 232
1.0
3 234
1.0
3 237
1.0
3 23

3 219
1.0
3 220
1.0
3 221
1.0
3 223
1.0
3 228
1.0
3 234
1.0
3 236
1.0
3 245
1.0
3 252
1.0
3 256
1.0
3 261
1.0
3 272
1.0
3 278
1.0
3 281
1.0
3 283
1.0
3 284
1.0
3 289
1.0
3 295
1.0
3 297
1.0
3 304
1.0
3 305
1.0
3 312
1.0
3 317
1.0
3 338
1.0
3 341
1.0
3 346
1.0
3 354
1.0
3 361
1.0
3 362
1.0
3 386
1.0
3 389
1.0
3 394
1.0
3 397
1.0
3 399
1.0
3 400
1.0
3 417
1.0
3 420
1.0
3 421
1.0
3 450
1.0
3 451
1.0
3 456
1.0
3 461
1.0
3 464
1.0
3 475
1.0
3 494
1.0
3 508
1.0
3 514
1.0
3 518
1.0
3 547
1.0
3 561
1.0
3 570
1.0
3 572
1.0
3 580
1.0
3 583
1.0
3 595
1.0
3 614
1.0
3 622
1.0
3 628
1.0
3 636
1.0
3 647
1.0
3 697
1.0
3 698
1.0
3 712
1.0
3 713
1.0
3 731
1.0
3 736
1.0
3 744
1.0
3 750
1.0
3 755
1.0
3 775
1.0
3 776
1.0
3 780
1.0
3 784
1.0
3 963
1.0
3 971
1.0
3 976
1.0
3 1035
1.0
3 1036
1.0
3 1042
1.0
3 1050
1.0
3 1073
1.0
3 1099
1.0
3 1110
1.0
3 1112
1.0
3 1115
1.0
3 1123
1.0
3 1125
1.0
3 1130
1.0
3 1133
1.0
3 1134
1.0
3 1137
1.0
3 1156
1.0
3 1159
1.0
3 1163
1.0
3 1183
1.0
3 1196
1.0
3 1219
1.0
3 1233
1.

...

293 679
1.0
293 683
1.0
293 696
1.0
293 697
1.0
293 698
1.0
293 700
1.0
293 707
1.0
293 711
1.0
293 713
1.0
293 715
1.0
293 720
1.0
293 725
1.0
293 734
1.0
293 739
1.0
293 756
1.0
293 758
1.0
293 759
1.0
293 763
1.0
293 767
1.0
293 768
1.0
293 778
1.0
293 781
1.0
293 783
1.0
293 788
1.0
293 791
1.0
293 808
1.0
293 812
1.0
293 822
1.0
293 836
1.0
293 841
1.0
293 843
1.0
293 851
1.0
293 852
1.0
293 853
1.0
293 854
1.0
293 859
1.0
293 864
1.0
293 868
1.0
293 875
1.0
293 877
1.0
293 880
1.0
293 889
1.0
293 899
1.0
293 902
1.0
293 905
1.0
293 907
1.0
293 909
1.0
293 911
1.0
293 913
1.0
293 917
1.0
293 932
1.0
293 934
1.0
293 938
1.0
293 947
1.0
293 952
1.0
293 969
1.0
293 982
1.0
293 1009
1.0
293 1011
1.0
293 1015
1.0
293 1022
1.0
293 1040
1.0
293 1069
1.0
293 1087
1.0
293 1096
1.0
293 1098
1.0
293 1099
1.0
293 1101
1.0
293 1121
1.0
293 1130
1.0
293 1134
1.0
293 1140
1.0
293 1141
1.0
293 1142
1.0
293 1144
1.0
293 1150
1.0
293 1156
1.0
293 1168
1.0
293 1173
1.0
293 1189
1.0
293 1211
1.0
293 

295 2392
1.0
295 2405
1.0
295 2409
1.0
295 2430
1.0
295 2439
1.0
295 2445
1.0
295 2446
1.0
295 2453
1.0
295 2482
1.0
295 2490
1.0
295 2501
1.0
295 2510
1.0
295 2514
1.0
295 2528
1.0
295 2535
1.0
295 2538
1.0
295 2578
1.0
295 2581
1.0
295 2594
1.0
295 2629
1.0
295 2658
1.0
295 2663
1.0
295 2675
1.0
295 2716
1.0
295 2726
1.0
295 2765
1.0
295 2779
1.0
295 2841
1.0
295 2866
1.0
295 2885
1.0
295 2900
1.0
295 2968
1.0
295 3004
1.0
295 3082
1.0
295 3134
1.0
295 3181
1.0
295 3235
1.0
295 3348
1.0
295 3355
1.0
295 3357
1.0
295 3399
1.0
295 6
1.0
295 13
1.0
295 18
1.0
295 20
1.0
295 27
1.0
295 28
1.0
295 31
1.0
295 34
1.0
295 36
1.0
295 52
1.0
295 55
1.0
295 60
1.0
295 61
1.0
295 67
1.0
295 73
1.0
295 74
1.0
295 87
1.0
295 92
1.0
295 109
1.0
295 110
1.0
295 114
1.0
295 115
1.0
295 128
1.0
295 136
1.0
295 139
1.0
295 152
1.0
295 158
1.0
295 175
1.0
295 177
1.0
295 191
1.0
295 192
1.0
295 194
1.0
295 197
1.0
295 199
1.0
295 201
1.0
295 215
1.0
295 220
1.0
295 228
1.0
295 236
1.0
295 242
1.0
295 25

298 344
1.0
298 347
1.0
298 350
1.0
298 361
1.0
298 365
1.0
298 368
1.0
298 373
1.0
298 377
1.0
298 386
1.0
298 389
1.0
298 392
1.0
298 403
1.0
298 404
1.0
298 410
1.0
298 415
1.0
298 419
1.0
298 420
1.0
298 425
1.0
298 455
1.0
298 457
1.0
298 463
1.0
298 472
1.0
298 480
1.0
298 481
1.0
298 483
1.0
298 490
1.0
298 494
1.0
298 500
1.0
298 504
1.0
298 507
1.0
298 508
1.0
298 514
1.0
298 531
1.0
298 537
1.0
298 540
1.0
298 546
1.0
298 547
1.0
298 555
1.0
298 560
1.0
298 562
1.0
298 566
1.0
298 570
1.0
298 573
1.0
298 604
1.0
298 607
1.0
298 636
1.0
298 639
1.0
298 647
1.0
298 674
1.0
298 692
1.0
298 706
1.0
298 716
1.0
298 729
1.0
298 736
1.0
298 749
1.0
298 751
1.0
298 755
1.0
298 765
1.0
298 778
1.0
298 780
1.0
298 797
1.0
298 801
1.0
298 815
1.0
298 831
1.0
298 844
1.0
298 848
1.0
298 874
1.0
298 904
1.0
298 918
1.0
298 922
1.0
298 928
1.0
298 930
1.0
298 942
1.0
298 944
1.0
298 946
1.0
298 947
1.0
298 950
1.0
298 971
1.0
298 981
1.0
298 986
1.0
298 999
1.0
298 1017
1.0
298 1022
1.0
29

300 104
1.0
300 106
1.0
300 110
1.0
300 121
1.0
300 141
1.0
300 148
1.0
300 156
1.0
300 163
1.0
300 168
1.0
300 172
1.0
300 174
1.0
300 178
1.0
300 183
1.0
300 185
1.0
300 193
1.0
300 194
1.0
300 198
1.0
300 206
1.0
300 211
1.0
300 213
1.0
300 216
1.0
300 217
1.0
300 218
1.0
300 235
1.0
300 236
1.0
300 241
1.0
300 245
1.0
300 251
1.0
300 258
1.0
300 266
1.0
300 270
1.0
300 272
1.0
300 289
1.0
300 291
1.0
300 293
1.0
300 298
1.0
300 302
1.0
300 310
1.0
300 312
1.0
300 314
1.0
300 321
1.0
300 324
1.0
300 330
1.0
300 336
1.0
300 346
1.0
300 350
1.0
300 352
1.0
300 370
1.0
300 371
1.0
300 379
1.0
300 380
1.0
300 382
1.0
300 387
1.0
300 392
1.0
300 416
1.0
300 417
1.0
300 420
1.0
300 422
1.0
300 428
1.0
300 432
1.0
300 434
1.0
300 435
1.0
300 436
1.0
300 455
1.0
300 466
1.0
300 476
1.0
300 481
1.0
300 486
1.0
300 493
1.0
300 494
1.0
300 502
1.0
300 507
1.0
300 510
1.0
300 512
1.0
300 520
1.0
300 522
1.0
300 523
1.0
300 524
1.0
300 532
1.0
300 536
1.0
300 541
1.0
300 542
1.0
300 545
1.0
300 

301 1693
1.0
301 1694
1.0
301 1704
1.0
301 1707
1.0
301 1711
1.0
301 1712
1.0
301 1729
1.0
301 1730
1.0
301 1736
1.0
301 1744
1.0
301 1777
1.0
301 1781
1.0
301 1782
1.0
301 1791
1.0
301 1792
1.0
301 1801
1.0
301 1814
1.0
301 1827
1.0
301 1829
1.0
301 1851
1.0
301 1852
1.0
301 1856
1.0
301 1864
1.0
301 1870
1.0
301 1889
1.0
301 1910
1.0
301 1913
1.0
301 1920
1.0
301 1922
1.0
301 1931
1.0
301 1932
1.0
301 1939
1.0
301 1953
1.0
301 1984
1.0
301 1993
1.0
301 1995
1.0
301 2003
1.0
301 2009
1.0
301 2011
1.0
301 2012
1.0
301 2030
1.0
301 2038
1.0
301 2070
1.0
301 2080
1.0
301 2086
1.0
301 2092
1.0
301 2093
1.0
301 2117
1.0
301 2120
1.0
301 2121
1.0
301 2137
1.0
301 2157
1.0
301 2163
1.0
301 2178
1.0
301 2181
1.0
301 2187
1.0
301 2191
1.0
301 2209
1.0
301 2212
1.0
301 2214
1.0
301 2245
1.0
301 2251
1.0
301 2254
1.0
301 2283
1.0
301 2296
1.0
301 2306
1.0
301 2323
1.0
301 2327
1.0
301 2333
1.0
301 2354
1.0
301 2364
1.0
301 2374
1.0
301 2377
1.0
301 2381
1.0
301 2392
1.0
301 2405
1.0
301 2409
1.0

In [257]:
np.savetxt('recom_matrix.csv', recom_matrix, delimiter=',')

In [258]:
'''저장된 recom_matrix 를 사용할 경우 실행함.'''
recom_matrix = pd.read_csv('recom_matrix.csv', header=None)

#### recom_matrix (predicted) 와 val_matrix (observed) 비교.<br></br>=> 각 user 별 vector 사이의 유사도를 계산하여 similairty_matrix 에 저장함.

In [259]:
# recom_matrix, val_matrix 의 비교를 편하게 하기 위해 product id 와 index 사이의 dictionary 를 만들고, 관리할 것임.
def swap_dictionary(original_dict):
    temp_dict = {}
    dict_list = original_dict.items()
    for i in dict_list:
        temp_dict[i[1]] = i[0]
    return temp_dict

In [260]:
tmp = products.to_dict()
swaped_products = swap_dictionary(tmp['Product_ID'])

In [261]:
# recom_matrix 에는 모든 product 가 column 으로 들어가 있음.
# new_recom 에는 val_matrix 에 있는 product 만 뽑아서 정리함.
# 이렇게 정리함으로써, new_recom 과 val_matrix 의 row vector 사이의 유사도를 계산할 수 있음. (차원을 맞춰 줌.)

new_recom = pd.DataFrame()

for product in val_products['Product_ID']:
    tmp = recom_matrix[swaped_products[product]]
    tmp = tmp.to_frame(name=product)
    new_recom = pd.merge(new_recom, tmp, left_index=True, right_index=True, how="outer")

In [262]:
# similarity matrix 를 정의하고, new_recom 과 val_matrix 의 row vector 사이의 유사도를 계산하여 저장함.

similarity_matrix = np.zeros(shape=(val_users_length, 1))

for i, user1 in enumerate(val_user_info['User_ID']):
    user_recom = np.array(new_recom.loc[i]).astype(int)
    user_val = np.array(val_matrix.loc[user1])
    similarity_matrix[i] = cos_sim(user_recom, user_val)
    
similarity_matrix = pd.DataFrame(similarity_matrix)
# similarity_matrix 의 index 는 users 의 index 와 같으며, users 를 통해 user_ID 로 접근할 수 있다.

0 결과가 나온 것은, user_recom, user_val 둘 중 하나의 norm 이 0 인 경우도 포함.

In [263]:
similarity_matrix.describe()

0
count  312.000000
mean     0.030747
std      0.028703
min      0.000000
25%      0.000000
50%      0.026514
75%      0.052773
max      0.107000

가장 유사도가 높은 것은 0.08임!!!! 즉, 1606 개의 product 중 128 개 정도의 product 를 맞춘 것이라고 할 수 잇음.

In [264]:
val_products_length

1606